# Gaussian mixture model

This notebook will be investigating the proper clustering method based on the results from Feature_Selection notebook. This notebook show some potential that the dimension reduction by feature selection and PCA show some potential that this could have some potential even with visual clustering.
Therefore we will be investigating sophisticated method of clustering and it will improve based on this result.






In [89]:
import os
# Set the environment variable
os.environ['OMP_NUM_THREADS'] = '1'

import pandas as pd
from sklearn.mixture import GaussianMixture
import plotly.express as px
import matplotlib.pyplot as plt
import numpy as np
from sklearn.preprocessing import StandardScaler
import seaborn as sns


import matplotlib.pyplot as plt
import seaborn as sns
import random
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the data

In [90]:
# Read CSV files into DataFrames
df_mi_corr = pd.read_csv("../processed_data/lazy_corr_MI_10_FS.csv")
df_mi_corr_50 = pd.read_csv("../processed_data/lazy_corr_MI_50_FS.csv")
df_corr = pd.read_csv("../processed_data/lazy_corr_FS.csv")
df_mi = pd.read_csv("../processed_data/batch_corr_MI_10_FS.csv")
df = pd.read_csv("../processed_data/batch_corr_FS.csv")
df_mi_50= pd.read_csv("../processed_data/batch_corr_MI_50_FS.csv")


df_corr_scaled_mi_batch_50= pd.read_csv("../processed_data/batch_corr_batch_MI_50_FS.csv")

df_corr_scaled_nomiddle= pd.read_csv("../processed_data/batch_corr_MI_nomiddle_50_FS.csv")

df_corr_scaled_mi_nofreq_50= pd.read_csv("../processed_data/batch_corr_MI_nofreq_50_FS.csv")

First we will be investigating df_mi and df_mi_50 that had good visualization result using PCA. Following figures were the results:

<img src="Figures\MI-batch Correlation with top 10 features_2D.png" alt="sphx_glr_plot_cluster_comparison_001" width="1500"/>
<img src="Figures\MI-batch Correlation with top 10 features_3d.png" alt="sphx_glr_plot_cluster_comparison_001" width="1500"/>

Based on the analytics and the nature of the clustering method where we want to find anomalies Gaussian Mixture model will be first thing to be investigated. 

<img src="https://scikit-learn.org/stable/_images/sphx_glr_plot_cluster_comparison_001.png" alt="sphx_glr_plot_cluster_comparison_001" width="1200"/>


# Gaussian Mixture Model 

Gaussian Mixture Models (GMM) can be used for anomaly detection by identifying data points that do not fit well into any of the Gaussian distributions modeled by the GMM. These points are considered anomalies because they have a low probability of belonging to any of the clusters.



In [91]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture
import plotly.express as px

def tune_gmm(data, n_components_range=range(1, 15), criterion='AIC'):
    """
    Perform hyperparameter tuning for a Gaussian Mixture Model (GMM),
    store the results in a DataFrame, visualize the results, and return the best model.

    Parameters:
    - data: pd.DataFrame - The input data for GMM clustering.
    - n_components_range: range - The range of number of components to try.
    - criterion: str - The criterion to use for selecting the best model ('AIC' or 'BIC').

    Returns:
    - best_model: GaussianMixture - The best GMM model based on the chosen criterion.
    - results_df: pd.DataFrame - The DataFrame containing AIC and BIC values for each model.
    """
    
    # Standardize the features
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(data)

    # Create lists to store the results
    aic_values = []
    bic_values = []
    n_components_list = []

    # Loop over the range of components
    for n_components in n_components_range:
        gmm = GaussianMixture(n_components=n_components, random_state=42)
        gmm.fit(features_scaled)
        
        aic = gmm.aic(features_scaled)
        bic = gmm.bic(features_scaled)
        
        aic_values.append(aic)
        bic_values.append(bic)
        n_components_list.append(n_components)

    # Create a DataFrame to store the results
    results_df = pd.DataFrame({
        'n_components': n_components_list,
        'AIC': aic_values,
        'BIC': bic_values
    })

    # Plot AIC and BIC values
    fig = px.line(results_df, x='n_components', y=['AIC', 'BIC'], 
                  title='AIC and BIC values for different number of components',
                  labels={'value': 'Score', 'n_components': 'Number of Components'},
                  markers=True)
    fig.show()

    # Find the best model based on the chosen criterion
    if criterion == 'AIC':
        best_index = results_df['AIC'].idxmin()
    elif criterion == 'BIC':
        best_index = results_df['BIC'].idxmin()
    else:
        raise ValueError("Criterion must be either 'AIC' or 'BIC'")

    best_model = GaussianMixture(n_components=results_df.loc[best_index, 'n_components'], random_state=42)
    best_model.fit(features_scaled)

    return best_model, results_df


The train_GMM function is designed to perform clustering on a dataset using a Gaussian Mixture Model (GMM). It not only fits the model and predicts cluster labels but also provides options for visualizing the clustering results in both 2D and 3D spaces using dimensionality reduction techniques like PCA or t-SNE.

The workflow looks like following

Workflow Overview

Data Preparation:

- Copy Data: To avoid modifying the original DataFrame.
- Extract Sensor IDs: If 'Sensor ID' exists, extract it for labeling in plots.
- Feature Scaling: Standardize features using StandardScaler for better model performance.

Model Training:

- Initialize GMM: Create a GaussianMixture instance with specified parameters.
- Fit Model: Train the GMM on the scaled features.
- Predict Clusters: Assign each data point to a cluster.
Evaluation Metrics:

- Cluster Distribution: Display the number of sensors in each cluster.
- Model Assessment: Calculate BIC and AIC to evaluate model fit.

Visualization:

- Dimensionality Reduction:
PCA: Preserves global structures; faster computation.
t-SNE: Captures local neighborhood structures; computationally intensive.
- Plotting:
2D or 3D Scatter Plot: Based on plot_3d, generates interactive plots using Plotly.
Hover Information: Displays 'Sensor ID' when hovering over data points.

In [92]:
best_gmm_model, tuning_results = tune_gmm(df_mi, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)


GaussianMixture(n_components=14, random_state=42)


Picked best number of component with elbow method and it is seems to be 6

## Perform Cluster

Bsaed on the elbow method we will be pick number of component that seems to be well performing.

In [93]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn.metrics import silhouette_score
import plotly.express as px


def train_GMM(df, n_components=5, random_state=42, visualization_method='PCA', plot_3d=False):
    """
    Train a Gaussian Mixture Model (GMM) on the given dataframe, predict clusters, and visualize the results.

    Parameters:
    df (DataFrame): The DataFrame containing the features to cluster.
    n_components (int): The number of clusters/components for the GMM.
    random_state (int): Random state for reproducibility.
    visualization_method (str): The method for visualization ('PCA' or 'TSNE').
    plot_3d (bool): Whether to generate a 3D plot. If False, a 2D plot will be generated.

    Returns:
    DataFrame: The original DataFrame with an additional column for cluster labels.
    GaussianMixture: The fitted GMM model.
    """

    # Standardize the features
    df = df.copy()
    sensor_ids = df.index if 'Sensor ID' not in df.columns else df['Sensor ID']
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(df.drop(columns=['Sensor ID']))

    # Fit a Gaussian Mixture Model
    gmm = GaussianMixture(n_components=n_components, random_state=random_state)
    gmm.fit(features_scaled)

    # Predict cluster labels
    cluster_labels = gmm.predict(features_scaled)
    df['cluster'] = cluster_labels

    # Calculate Silhouette Score
    silhouette_avg = silhouette_score(features_scaled, cluster_labels)
    

    print("============ Distribution of Sensors in each Cluster ============")
    print(df.groupby(["cluster"])["Sensor ID"].count())

    # Evaluate the model using BIC and AIC
    bic = gmm.bic(features_scaled)
    aic = gmm.aic(features_scaled)

    print(f"BIC: {bic}")
    print(f"AIC: {aic}")
    print(f"Silhouette Score: {silhouette_avg:.4f}")

    # Visualize the clustering results using PCA or t-SNE
    if visualization_method.upper() == 'PCA':
        n_components = 3 if plot_3d else 2
        pca = PCA(n_components=n_components)
        components = pca.fit_transform(features_scaled)
        title = '3D Visualization using PCA' if plot_3d else '2D Visualization using PCA'
    elif visualization_method.upper() == 'TSNE':
        n_components = 3 if plot_3d else 2
        tsne = TSNE(n_components=n_components, random_state=random_state)
        components = tsne.fit_transform(features_scaled)
        title = '3D Visualization using t-SNE' if plot_3d else '2D Visualization using t-SNE'
    else:
        raise ValueError("visualization_method should be either 'PCA' or 'TSNE'.")

    # Create a DataFrame for the components
    components_df = pd.DataFrame(components, columns=[f'Component {i+1}' for i in range(n_components)])
    components_df['cluster'] = cluster_labels
    components_df['Sensor ID'] = sensor_ids

    # Plot the results
    if plot_3d:
        fig = px.scatter_3d(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            z='Component 3', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    else:
        fig = px.scatter(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    
    fig.show()

    return df, gmm



The train_GMM function is designed to perform clustering on a dataset using a Gaussian Mixture Model (GMM). It fits the model to the data, predicts cluster labels, evaluates the model, and visualizes the clustering results using dimensionality reduction techniques like PCA or t-SNE.

## Evaluation Methods
One of the hard thing about the clustering is how to evaluate the clustering. To do so we will leverage the nature of our dataset.

weighted average of average variability of pingtime: This will reveals the how much variability within the cluster. This does not compare each cluster's quality and having more cluster is always better but this doesn't account that either.


In [94]:
# Load the dataset
file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
all_cleaned_df = pd.read_csv(file_path)
all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)

In [95]:
def identify_outliers(series):
    Q1 = series.quantile(0.25)
    Q3 = series.quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return ((series < lower_bound) | (series > upper_bound)).sum()

def average_variability_metrics(df_cluster, all_cleaned_df):
    """
    Calculate the average number of outliers and average standard deviation of ping time for each cluster,
    and the weighted averages of these values.

    Parameters:
    df_cluster (DataFrame): The DataFrame containing sensor ID and their respective clusters.
    all_cleaned_df (DataFrame): The DataFrame containing the cleaned data.

    Returns:
    DataFrame: A DataFrame with columns for cluster, average number of outliers, and average std ping time.
    float: The weighted average of the average number of outliers across clusters.
    float: The weighted average of the average standard deviation of ping time across clusters.
    """

    # List to store the results
    results = []

    # Iterate over each cluster
    for target in df_cluster["cluster"].unique():
        # Get the sensor IDs for the current cluster
        cluster_sensors = df_cluster[df_cluster["cluster"] == target]["Sensor ID"].unique()

        # Filter the all_cleaned_df for the current cluster sensors
        all_cleaned_df_target = all_cleaned_df[all_cleaned_df['Sensor ID'].isin(cluster_sensors)]

        # Group by 'Delay (us)' and 'Range (cm)', then calculate the number of outliers in 'Ping Time (us)'
        grouped_outliers = all_cleaned_df_target.groupby(['Delay (us)', 'Range (cm)'])['Ping Time (us)'].apply(identify_outliers).reset_index(name='outliers')
        
        # Calculate the average number of outliers for the current cluster
        avg_count_outliers = grouped_outliers['outliers'].mean()
        max_count_outliers = grouped_outliers['outliers'].max()

        # Group by sensor ID, delay, and range, then calculate the standard deviation of ping time
        grouped_std = all_cleaned_df_target.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
            std_ping_time=('Ping Time (us)', 'std')
        ).reset_index()

        # Calculate the average std ping time for the current cluster
        avg_std_ping_time = grouped_std['std_ping_time'].mean()

        # Append the results to the list
        results.append({'cluster': target, 'max_count_outliers':max_count_outliers, 'avg_count_outliers': avg_count_outliers, 'avg_std_ping_time': avg_std_ping_time, 'count': len(cluster_sensors)})
    
    # Convert the results list to a DataFrame
    results_df = pd.DataFrame(results)
    
    # Calculate the weighted average of the average number of outliers
    alpha = 0.5

    results_df['weighted_avg_count_outliers'] =(results_df['max_count_outliers']-results_df['avg_count_outliers']) /results_df['count']
    weighted_avg_count_outliers_score = results_df['weighted_avg_count_outliers'].mean() + alpha*np.log(results_df['cluster'].max() + 1)

    # Calculate the weighted average of the average std ping time
    results_df['weighted_avg_std_ping_time'] = results_df['avg_std_ping_time'] /results_df['count']
    weighted_avg_std_ping_time_score = results_df['weighted_avg_std_ping_time'].mean()+ alpha*np.log(results_df['cluster'].max() + 1)

    return results_df, weighted_avg_count_outliers_score, weighted_avg_std_ping_time_score



#### Understanding the scoring methods

The average_variability_metrics function calculates two primary metrics for evaluating cluster performance:

**Weighted Average Outlier Score (weighted_avg_count_outliers_score):**

- Purpose: Measures the relative consistency of data within clusters by assessing the deviation of outlier counts from the maximum possible outliers in the cluster.

- Weighted Outlier Score for Cluster i = (Max Count of Outliers_i - Average Count of Outliers_i) / Number of Sensors in Cluster i

The overall weighted_avg_count_outliers_score is the mean of these scores across all clusters.

Rationale: 
- Max Count of Outliers vs. Average Count of Outliers: By subtracting the average count from the maximum, we assess how much the cluster deviates from its worst-case scenario
- Normalization by Cluster Size: Dividing by the number of sensors accounts for cluster size differences, ensuring comparability across clusters.


**Weighted Average Standard Deviation Score (weighted_avg_std_ping_time_score):**

- Purpose: Evaluates the variability of ping times within clusters, adjusted for cluster size and index.

- Weighted Std Dev Score for Cluster i = (Average Std Dev of Ping Time_i / Number of Sensors in Cluster i) * (Cluster Index i + 1)

The overall weighted_avg_std_ping_time_score is the mean of these scores across all clusters.


Rationale: 
- Average Std Dev of Ping Time: Reflects the typical variability in ping times within the cluster.
- Adjustment by Cluster Size and Index: Dividing by cluster size normalizes for the number of sensors, and multiplying by (cluster + 1) gives weight to clusters with higher indices, potentially reflecting their relative importance or order.

In [96]:
df_mi_gmm_8,gmm_8 = train_GMM(df_mi, n_components=8, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    151
1     17
2     20
3      1
4      1
5      1
6      1
7     18
Name: Sensor ID, dtype: int64
BIC: 728.0219188083929
AIC: -1035.903749879713
Silhouette Score: 0.3319


In [97]:
results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df_mi_gmm_8,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        7                 119           20.377778          19.304321     18   
1        0                1128          552.355556          47.569719    151   
2        6                  23            5.400000          26.583564      1   
3        2                 323           53.400000         305.171276     20   
4        1                 140           28.577778         619.375891     17   
5        4                  19            4.644444          13.420619      1   
6        5                  22            2.622222         380.734807      1   
7        3                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     5.479012                    1.072462  
1                     3.812215                    0.315031  
2                    17.600000                   26.583564  
3                    13.480000                   15.258564  
4                     6.554248                   36.433876  
5                    14.355556                   13.420619  
6                    19.377778                  380.734807  
7                    19.422222                   16.225759

Based on this evaluation method we can do gridsearch on the n_component and also performs elbow method.

In [98]:
from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture
from sklearn.metrics import silhouette_score

def search_gmm_weighted_avg(df, data, n_components_range=range(2, 20)):
    for i in n_components_range:
        # Standardize the features
        scaler = StandardScaler()
        features_scaled = scaler.fit_transform(df)

        # Fit a Gaussian Mixture Model
        gmm = GaussianMixture(n_components=i, random_state=42)
        gmm.fit(features_scaled)

        # Predict cluster labels
        cluster_labels = gmm.predict(features_scaled)
        df['cluster'] = cluster_labels

        # Compute silhouette score
        sil_score = silhouette_score(features_scaled, cluster_labels)

        # Compute your custom metrics
        results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df, data)

        print(f"Weighted average of variability score: {weighted_avg_std_ping_time_score} Outlier score: {weighted_avg_outliers_score} Silhouette Score: {sil_score:.4f}")

# Call the function with your data
search_gmm_weighted_avg(df_mi, all_cleaned_df)


Weighted average of variability score: 5.321287756908612 Outlier score: 4.277129145835528 Silhouette Score: 0.3592
Weighted average of variability score: 12.88106624335185 Outlier score: 9.051261235313536 Silhouette Score: 0.4260
Weighted average of variability score: 11.253558063555257 Outlier score: 10.466913405064295 Silhouette Score: 0.4031
Weighted average of variability score: 18.176329756070334 Outlier score: 11.505489999988095 Silhouette Score: 0.2921
Weighted average of variability score: 11.303717462690942 Outlier score: 10.89521916062012 Silhouette Score: 0.0522
Weighted average of variability score: 10.447689101920473 Outlier score: 9.612023239786296 Silhouette Score: 0.2825
Weighted average of variability score: 54.65434752859516 Outlier score: 11.724132507651703 Silhouette Score: 0.1307
Weighted average of variability score: 52.47661849094265 Outlier score: 12.883533108951019 Silhouette Score: 0.2625
Weighted average of variability score: 50.96524681830953 Outlier score: 

Evaluating Consistency Within Clusters:

- Low Outlier Scores: Indicate clusters where sensors behave consistently with fewer anomalies.

- Low Standard Deviation Scores: Suggest that sensors within the cluster have similar ping time variability.

Based on the result we will be investigating the when n component is 7 and 11.

### Visual Investigate Clustering performance

In [99]:
def visualize_lineplot_ping_time_with_variability(df, target = []):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    for delay in unique_delays:
        subset_df = target_df[target_df['Delay (us)'] == delay]

        fig = px.line(

        )

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                )
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            )
        )

        fig.update_layout(
            xaxis_title='Range (cm)',
            yaxis_title='Mean Ping Time (us)',
            legend_title='Sensor ID',
            template='plotly_white'
        )

        fig.show()


This function visualizes the effect of range on ping time for each delay setting, including error bars to represent the variability in measurements (standard deviation). The function also plots a reference line for comparison.

In [100]:
def visualize_lineplot_ping_time_with_variability_simple(df, target=[]):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    target (list): List of target sensor IDs to visualize.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    # Define the number of columns for subplots
    num_columns = 2  # 2 columns for the grid
    num_rows = 3  # 3 rows for the grid

    # Create subplots
    fig = make_subplots(rows=num_rows, cols=num_columns, subplot_titles=[f'Delay: {delay} us' for delay in unique_delays])

    for i, delay in enumerate(unique_delays):
        subset_df = target_df[target_df['Delay (us)'] == delay]

        # Get the row and column position for the subplot
        row = (i // num_columns) + 1
        col = (i % num_columns) + 1

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                ),
                row=row, col=col
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            ),
            row=row, col=col
        )

    fig.update_layout(
        height=1500,  # Adjust height for the grid layout
        width=1500,  # Adjust width for the grid layout
        showlegend=False,
        title_text="Ping Time vs Range for Different Delays"
    )

    fig.show()


This function provides a simpler, more compact visualization of the effect of range on ping time, by displaying multiple line plots (with error bars) in a grid of subplots. This helps compare data for multiple delays in one figure.

In [101]:
def visualize_cluster(df,cluster = 0, simple = True):
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)
    
    cluster_sensors = df[df["cluster"]==cluster]["Sensor ID"].unique()
    if simple:
        visualize_lineplot_ping_time_with_variability_simple(all_cleaned_df,cluster_sensors)
    else:
        visualize_lineplot_ping_time_with_variability(all_cleaned_df,cluster_sensors)

This function allows visualization of ping time data for sensors belonging to a specific cluster, with an option to choose between the simpler subplot view or individual line plots.

## Test df_mi 

### Investigate df_mi with n_components 7 

Training the model

In [102]:
df_mi_gmm_7,gmm_7 = train_GMM(df_mi, n_components=7, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    56
1    98
2    13
3    25
4     1
5    16
6     1
Name: Sensor ID, dtype: int64
BIC: 2019.3547706175896
AIC: 195.1811663765693
Silhouette Score: 0.3525


In [103]:
search_gmm_weighted_avg(df_mi,all_cleaned_df)

Weighted average of variability score: 5.321287756908612 Outlier score: 4.277129145835528 Silhouette Score: 0.3277
Weighted average of variability score: 12.88106624335185 Outlier score: 9.051261235313536 Silhouette Score: 0.4260
Weighted average of variability score: 11.253558063555257 Outlier score: 10.466913405064295 Silhouette Score: 0.4031
Weighted average of variability score: 18.176329756070334 Outlier score: 11.505489999988095 Silhouette Score: 0.2921
Weighted average of variability score: 11.303717462690942 Outlier score: 10.89521916062012 Silhouette Score: 0.0522
Weighted average of variability score: 10.447689101920473 Outlier score: 9.612023239786296 Silhouette Score: 0.2825
Weighted average of variability score: 54.65434752859516 Outlier score: 11.724132507651703 Silhouette Score: 0.1307
Weighted average of variability score: 52.47661849094265 Outlier score: 12.883533108951019 Silhouette Score: 0.2625
Weighted average of variability score: 50.96524681830953 Outlier score: 

In [104]:
results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df_mi_gmm_7,all_cleaned_df)

print(weighted_avg_outliers_score, weighted_avg_std_ping_time_score)
results_df

10.427788931147226 8.872305552261727


cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        5                 119           16.177778          20.468185     16   
1        2                 173           54.355556          38.731820     13   
2        1                 665          130.822222         102.385542     98   
3        0                 261           70.466667          22.074261     56   
4        3                 244           44.000000         498.787720     25   
5        6                  19            4.644444          13.420619      1   
6        4                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.426389                    1.279262  
1                     9.126496                    2.979371  
2                     5.450794                    1.044750  
3                     3.402381                    0.394183  
4                     8.000000                   19.951509  
5                    14.355556                   13.420619  
6                    19.422222                   16.225759

#### Cluster 3: Majority cluster 



In [105]:
visualize_cluster(df_mi_gmm_7,3)

#### Cluster 0: another majority cluster

In [106]:
visualize_cluster(df_mi_gmm_7,0)

#### Cluster 2: decent sized cluster

In [107]:
visualize_cluster(df_mi_gmm_7,2)

From this visualziation it showed the potential where comparing the cluster 0 and 2's wehn delay 10000 cluster 0 seems to be cluster of over measuring and cluster 2 is under measuring 

Idea for feature engineering: we can have like a slope 


In [108]:
visualize_cluster(df_mi_gmm_7,1)

In [109]:
visualize_cluster(df_mi_gmm_7,5)

### Investigate df_mi with 11 n_components

Training the model

In [110]:
df_mi_gmm_11,gmm_11 = train_GMM(df_mi, n_components=11, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0     58
1     87
2     13
3     13
4      1
5      1
6     16
7     18
8      1
9      1
10     1
Name: Sensor ID, dtype: int64
BIC: 2561.543730511781
AIC: -306.9274233130893
Silhouette Score: 0.4303


#### Cluster 3: majority cluster

In [111]:
visualize_cluster(df_mi_gmm_11,3)

#### Cluster 0: another majority cluster

In [112]:
visualize_cluster(df_mi_gmm_11,0)

#### Cluster 10: another majority cluster

In [113]:
visualize_cluster(df_mi_gmm_11,10)

## Test df_mi_50

Training the model

In [114]:
best_gmm_model, tuning_results = tune_gmm(df_mi_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=13, random_state=42)


Test n_component 10 and 13

In [115]:
search_gmm_weighted_avg(df_mi_50,all_cleaned_df)

Weighted average of variability score: 3.683040055271788 Outlier score: 7.7182819100895586 Silhouette Score: 0.1517
Weighted average of variability score: 3.334571683702152 Outlier score: 8.154396483414988 Silhouette Score: 0.0464
Weighted average of variability score: 4.481051992668229 Outlier score: 7.821034206305203 Silhouette Score: 0.0381
Weighted average of variability score: 9.281671972224151 Outlier score: 7.64809283398913 Silhouette Score: 0.0609
Weighted average of variability score: 4.574294984289398 Outlier score: 7.2646174599326185 Silhouette Score: 0.0261
Weighted average of variability score: 6.510476952030552 Outlier score: 7.734182450575879 Silhouette Score: 0.0280
Weighted average of variability score: 6.396906776159947 Outlier score: 8.953840807182177 Silhouette Score: 0.0274
Weighted average of variability score: 8.465925671860015 Outlier score: 8.652123103562445 Silhouette Score: 0.0214
Weighted average of variability score: 14.659772468119325 Outlier score: 10.659

### Investigate df_mi_50 with 13 n_components

In [116]:
df_mi_50_gmm_13,mi_50_gmm_13 = train_GMM(df_mi_50, n_components=13, random_state=42,visualization_method='TSNE',plot_3d=True)

============ Distribution of Sensors in each Cluster ============
cluster
0     12
1     16
2     24
3     10
4     21
5     42
6     17
7     17
8     14
9      1
10     3
11    22
12    11
Name: Sensor ID, dtype: int64
BIC: 32319.70231907729
AIC: -27637.034878664723
Silhouette Score: 0.0372


In [117]:
df_mi_50_gmm_13,mi_50_gmm_13 = train_GMM(df_mi_50, n_components=13, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0     12
1     16
2     24
3     10
4     21
5     42
6     17
7     17
8     14
9      1
10     3
11    22
12    11
Name: Sensor ID, dtype: int64
BIC: 32319.70231907729
AIC: -27637.034878664723
Silhouette Score: 0.0372


In [118]:
results_df, _,_ = average_variability_metrics(df_mi_50_gmm_13,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        11                 187           48.911111          22.425665     22   
1        12                 250           71.533333          44.642995     11   
2         8                  58           30.288889          26.009047     14   
3         0                 143           18.622222          14.504102     12   
4         4                 165           29.022222         136.252529     21   
5         3                  94           18.600000         234.767292     10   
6         5                 291           46.733333          71.415563     42   
7         2                 111           20.311111          59.173938     24   
8         6                 156           55.288889          11.747254     17   
9         7                 150           27.733333         161.713090     17   
10       10                  59            5.733333         605.100547      3   
11        1                 156           28.711111         541.794678     16   
12        9                  23            3.577778          16.225759      1   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                      6.276768                    1.019348  
1                     16.224242                    4.058454  
2                      1.979365                    1.857789  
3                     10.364815                    1.208675  
4                      6.475132                    6.488216  
5                      7.540000                   23.476729  
6                      5.815873                    1.700371  
7                      3.778704                    2.465581  
8                      5.924183                    0.691015  
9                      7.192157                    9.512535  
10                    17.755556                  201.700182  
11                     7.955556                   33.862167  
12                    19.422222                   16.225759

In [119]:
#visualize_cluster(df_mi_50_gmm_13,1)

From this visualization we can see they are grouped where it trouble detecting at delay 16800 range 13.

## Test df_corr_scaled_mi_batch_50

Training the model

In [120]:
best_gmm_model, tuning_results = tune_gmm(df_corr_scaled_mi_batch_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=14, random_state=42)


In [121]:
search_gmm_weighted_avg(df_corr_scaled_mi_batch_50,all_cleaned_df)

Weighted average of variability score: 3.2350204009159738 Outlier score: 7.150707488243273 Silhouette Score: 0.1226
Weighted average of variability score: 3.6481903951764862 Outlier score: 7.692794344426407 Silhouette Score: 0.0454
Weighted average of variability score: 2.81513791228401 Outlier score: 8.979379098582186 Silhouette Score: 0.0499
Weighted average of variability score: 10.252462731926189 Outlier score: 7.82766394684246 Silhouette Score: 0.0484
Weighted average of variability score: 9.604567244176037 Outlier score: 8.923544497164611 Silhouette Score: 0.0491
Weighted average of variability score: 20.01028531707462 Outlier score: 10.774811057306946 Silhouette Score: 0.0392
Weighted average of variability score: 15.91197140371629 Outlier score: 8.207862038874755 Silhouette Score: 0.0381
Weighted average of variability score: 12.267071538819028 Outlier score: 7.566850495363106 Silhouette Score: 0.0309
Weighted average of variability score: 16.40599785916099 Outlier score: 7.987

Test n_component 10 and 15 based on the score result

In [122]:
df_corr_scaled_mi_batch_50_gmm_10,mi_batch_gmm_10 = train_GMM(df_corr_scaled_mi_batch_50, n_components=10, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    17
1    15
2    20
3    30
4    16
5    32
6    20
7    39
8    20
9     1
Name: Sensor ID, dtype: int64
BIC: 21002.948950586986
AIC: -25116.84571516901
Silhouette Score: 0.0334


In [123]:
results_df, _,_ = average_variability_metrics(df_corr_scaled_mi_batch_50_gmm_10,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        6                 149           22.444444          17.479789     20   
1        2                 314           44.822222          32.185802     20   
2        0                 143           32.511111          42.833711     17   
3        8                 165           24.333333         116.251328     20   
4        5                 245           41.644444         150.100719     32   
5        4                 110           29.422222          29.080173     16   
6        3                 201           34.822222         136.069175     30   
7        7                 219           35.400000          41.848902     39   
8        1                 158           34.244444         636.990687     15   
9        9                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.327778                    0.873989  
1                    13.458889                    1.609290  
2                     6.499346                    2.519630  
3                     7.033333                    5.812566  
4                     6.354861                    4.690647  
5                     5.036111                    1.817511  
6                     5.539259                    4.535639  
7                     4.707692                    1.073049  
8                     8.250370                   42.466046  
9                    19.422222                   16.225759

#### cluster 9: outliers

First thing that I want to look into is Cluster 9 where it has a individual score of 102.
Lower is better but this may not be always true for all since some cluster is just cluster of outliers

In [124]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,9)

as we can see this cluster is compose of outlier that have outgoing on 16800 range 13

#### Cluster 5: var score 12.607090

In [125]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,5)

Notice they all at range 13, 18, 33,and 38 have over measurement.

#### Cluter 7: majority cluster 

num: 31 score :19.081381

In [126]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,7)

#### Cluster 0: with low score
0	44.284186	16	2.767762

In [127]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,0)

more of constant over measurment but there are some noticable outliers

## Test df_corr_scaled_mi_nofreq_50

Training the model

In [128]:
best_gmm_model, tuning_results = tune_gmm(df_corr_scaled_mi_nofreq_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=11, random_state=42)


In [129]:
search_gmm_weighted_avg(df_corr_scaled_mi_nofreq_50,all_cleaned_df)

Weighted average of variability score: 3.566662661514761 Outlier score: 7.772630821649065 Silhouette Score: 0.1502
Weighted average of variability score: 5.666166690545439 Outlier score: 8.599983861678439 Silhouette Score: 0.0601
Weighted average of variability score: 4.761973955432798 Outlier score: 7.662417989830755 Silhouette Score: 0.0547
Weighted average of variability score: 5.905193388456394 Outlier score: 8.10001938119336 Silhouette Score: 0.0547
Weighted average of variability score: 11.203169527028805 Outlier score: 10.933153386402969 Silhouette Score: 0.0690
Weighted average of variability score: 11.112248268019043 Outlier score: 11.14250334760534 Silhouette Score: 0.0790
Weighted average of variability score: 21.72987930445944 Outlier score: 8.81824114443651 Silhouette Score: 0.0483
Weighted average of variability score: 14.921206339532441 Outlier score: 8.644846297034764 Silhouette Score: 0.0291
Weighted average of variability score: 8.545208843040053 Outlier score: 8.7229

Test n_component 10 and 15 based on the score result

Also test n_component = 9 and 16

### n_component = 10

In [130]:
df_nofreq_50_gmm_10,mi_nofreq_gmm_10 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=10, random_state=42, visualization_method='PCA', plot_3d=True)

============ Distribution of Sensors in each Cluster ============
cluster
0    20
1    22
2    24
3    47
4    10
5    20
6    32
7    12
8    15
9     8
Name: Sensor ID, dtype: int64
BIC: 22541.534038531354
AIC: -23578.26062722464
Silhouette Score: 0.0265


In [131]:
results_df_nofreq, _,_ = average_variability_metrics(df_nofreq_50_gmm_10,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        8                 233           49.822222          89.480497     15   
1        7                 196           65.755556          86.452427     12   
2        5                 253           60.711111         230.663512     20   
3        0                 109           30.155556          13.777298     20   
4        3                 314           67.933333          85.163121     47   
5        2                 231           23.288889          85.316253     24   
6        6                 237           78.555556          17.557155     32   
7        1                 196           52.755556          87.027326     22   
8        4                  59           10.888889         159.593444     10   
9        9                  88           10.266667         901.151450      8   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    12.211852                    5.965366  
1                    10.853704                    7.204369  
2                     9.614444                   11.533176  
3                     3.942222                    0.688865  
4                     5.235461                    1.811981  
5                     8.654630                    3.554844  
6                     4.951389                    0.548661  
7                     6.511111                    3.955788  
8                     4.811111                   15.959344  
9                     9.716667                  112.643931

#### Cluter 2: majority cluster 

In [132]:
target_cluster = 2
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
5        2                 231           23.288889          85.316253     24   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
5                      8.65463                    3.554844  


#### Cluster 7: cluster of under measurement and outliers

In [133]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
1        7                 196           65.755556          86.452427     12   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
1                    10.853704                    7.204369  


This cluster seems to be collection of under measurement and outliers

#### Cluster 6: over measurement and but with some outliers

In [134]:
target_cluster = 6
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
6        6                 237           78.555556          17.557155     32   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
6                     4.951389                    0.548661  


This cluster seems to be above measurement clusters

### Investigate other clusters 0,1,3,4,5,8,9

In [135]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
3        0                 109           30.155556          13.777298     20   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
3                     3.942222                    0.688865  


Cluster 0 seems to be over measurements

In [136]:
target_cluster = 1
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
7        1                 196           52.755556          87.027326     22   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
7                     6.511111                    3.955788  


In [137]:
target_cluster = 3
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
4        3                 314           67.933333          85.163121     47   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
4                     5.235461                    1.811981  


In [138]:
target_cluster = 4
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
8        4                  59           10.888889         159.593444     10   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
8                     4.811111                   15.959344  


In [139]:
target_cluster = 5
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
2        5                 253           60.711111         230.663512     20   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
2                     9.614444                   11.533176  


In [140]:
target_cluster = 8
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        8                 233           49.822222          89.480497     15   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    12.211852                    5.965366  


In [141]:
target_cluster = 9
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
9        9                  88           10.266667          901.15145      8   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
9                     9.716667                  112.643931  


### n_component = 15

In [142]:
df_nofreq_50_gmm_15,mi_nofreq_gmm_15 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=15, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0     16
1     23
2     18
3     30
4      9
5     12
6     15
7     11
8     16
9      7
10     3
11     1
12    15
13     1
14    33
Name: Sensor ID, dtype: int64
BIC: 41776.4378965934
AIC: -27404.92765580595
Silhouette Score: 0.0343


In [143]:
results_df_nofreq,_,_ = average_variability_metrics(df_nofreq_50_gmm_15,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0         8                 233           50.644444          84.516848     16   
1         7                 250           71.533333          44.642995     11   
2        14                 265           47.511111         169.461251     33   
3         0                 105           15.400000          14.935221     16   
4         3                 194           34.422222          83.193282     30   
5         2                 152           20.933333          14.769418     18   
6        12                  90           14.288889          14.085522     15   
7         6                 177           39.466667          17.230979     15   
8         1                 279           58.511111         141.346355     23   
9        10                  59            5.733333         605.100547      3   
10        4                  64           12.066667         176.329309      9   
11        5                 109           39.866667          84.933148     12   
12        9                  46            4.311111         853.812177      7   
13       11                  23            3.666667          29.022530      1   
14       13                  23            3.577778          16.225759      1   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     11.397222                    5.282303  
1                     16.224242                    4.058454  
2                      6.590572                    5.135189  
3                      5.600000                    0.933451  
4                      5.319259                    2.773109  
5                      7.281481                    0.820523  
6                      5.047407                    0.939035  
7                      9.168889                    1.148732  
8                      9.586473                    6.145494  
9                     17.755556                  201.700182  
10                     5.770370                   19.592145  
11                     5.761111                    7.077762  
12                     5.955556                  121.973168  
13                    19.333333                   29.022530  
14                    19.422222                   16.225759

#### Cluter 0:low ping time score

In [144]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
3        0                 105                15.4          14.935221     16   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
3                          5.6                    0.933451  


#### Cluter 14 and 3: compare aimilar count and similar ping time score

In [145]:
target_cluster = 14
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
2       14                 265           47.511111         169.461251     33   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
2                     6.590572                    5.135189  


In [146]:
target_cluster = 3
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
4        3                 194           34.422222          83.193282     30   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
4                     5.319259                    2.773109  


#### Cluter 2,6,and 5: compare majority cluster 

In [147]:
target_cluster = 6
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
7        6                 177           39.466667          17.230979     15   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
7                     9.168889                    1.148732  


In [148]:
target_cluster = 5
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

    cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
11        5                 109           39.866667          84.933148     12   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
11                     5.761111                    7.077762  


In [149]:
target_cluster = 2
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
5        2                 152           20.933333          14.769418     18   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
5                     7.281481                    0.820523  


As a result n_component 10 seems to be more promising so I will be investigating this further.

#### Investigate rest data points

In [150]:
target_cluster = 1
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
8        1                 279           58.511111         141.346355     23   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
8                     9.586473                    6.145494  


In [151]:
target_cluster = 4
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

    cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
10        4                  64           12.066667         176.329309      9   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
10                      5.77037                   19.592145  


In [152]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
1        7                 250           71.533333          44.642995     11   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
1                    16.224242                    4.058454  


In [153]:
target_cluster = 8
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        8                 233           50.644444          84.516848     16   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    11.397222                    5.282303  


### Test n_component 9

In [154]:
df_nofreq_50_gmm_9,mi_nofreq_gmm_9 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=9, random_state=42)

============ Distribution of Sensors in each Cluster ============
cluster
0    18
1    28
2    26
3    44
4    15
5    21
6    32
7    13
8    13
Name: Sensor ID, dtype: int64
BIC: 17767.974573209955
AIC: -23739.505915217378
Silhouette Score: 0.0180


In [155]:
results_df_nofreq,_,_ = average_variability_metrics(df_nofreq_50_gmm_9,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        8                 106           41.311111          60.307581     13   
1        7                 196           59.933333         174.611960     13   
2        5                 273           47.688889         255.808665     21   
3        0                 105           30.244444          13.916496     18   
4        3                 361           78.666667         146.449398     44   
5        2                 248           21.444444          79.434252     26   
6        6                 237           78.555556          17.557155     32   
7        1                 164           61.711111          77.961190     28   
8        4                 203           26.244444         311.336431     15   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     4.976068                    4.639045  
1                    10.466667                   13.431689  
2                    10.729101                   12.181365  
3                     4.153086                    0.773139  
4                     6.416667                    3.328395  
5                     8.713675                    3.055164  
6                     4.951389                    0.548661  
7                     3.653175                    2.784328  
8                    11.783704                   20.755762

#### Test major cluster 7 where it has low outlier score and moderate avg ping time score

In [156]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_9,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
1        7                 196           59.933333          174.61196     13   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
1                    10.466667                   13.431689  


In [157]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_9,target_cluster,simple=False)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
3        0                 105           30.244444          13.916496     18   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
3                     4.153086                    0.773139  


## Visualize based on cluster

In [158]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_lineplot_ping_time_with_variability_by_cluster(df, cluster_sensors, delay=None):
    """
    Visualize the effect of range on ping time for each cluster with variability, optionally filtering by delay.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    cluster_sensors (dict): Dictionary where keys are cluster labels and values are lists of sensor IDs in each cluster.
    delay (int, optional): If specified, only data for this delay will be plotted. Otherwise, all delays are plotted.
    """
    # Group by sensor ID, range, and delay, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Range (cm)', 'Delay (us)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    # Filter by the specified delay if provided
    if delay is not None:
        grouped_df = grouped_df[grouped_df['Delay (us)'] == delay]

    # Define the number of columns for subplots
    num_clusters = len(cluster_sensors)
    num_columns = 2  # Number of columns for the grid
    num_rows = (num_clusters + num_columns - 1) // num_columns  # Calculate rows based on the number of clusters

    # Create subplots
    fig = make_subplots(rows=num_rows, cols=num_columns, subplot_titles=[f'Cluster {cluster}' for cluster in cluster_sensors.keys()])

    for i, (cluster, sensors) in enumerate(cluster_sensors.items()):
        cluster_df = grouped_df[grouped_df['Sensor ID'].isin(sensors)]

        # Get the row and column position for the subplot
        row = (i // num_columns) + 1
        col = (i % num_columns) + 1

        # Adding error bars
        for sensor_id in sensors:
            sensor_data = cluster_df[cluster_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                ),
                row=row, col=col
            )

        # Plot reference line
        ranges = np.linspace(cluster_df['Range (cm)'].min(), cluster_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            ),
            row=row, col=col
        )

    fig.update_layout(
        height=3000,  # Adjust height for the grid layout
        width=1500,  # Adjust width for the grid layout
        showlegend=False,
        title_text=f"Ping Time vs Range for Different Clusters {delay}us"
    )

    fig.show()

def visualize_cluster_delay(df, delay_pos=4):
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0", axis=1)
    
    # Dictionary to store sensors grouped by cluster
    cluster_sensors = df.groupby("cluster")["Sensor ID"].apply(list).to_dict()

    delays = [3000,6000,8000,10000,16800]

    visualize_lineplot_ping_time_with_variability_by_cluster(all_cleaned_df, cluster_sensors, delays[delay_pos])



In [159]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_lineplot_ping_time_with_variability_side_by_side(df, cluster_sensors, delays):
    """
    Visualize the effect of range on ping time for selected clusters and delays side-by-side with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    cluster_sensors (dict): Dictionary where keys are cluster labels and values are lists of sensor IDs in each cluster.
    delays (list): List of delays to compare across clusters.
    """
    # Group by sensor ID, range, and delay, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Range (cm)', 'Delay (us)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    # Determine number of rows and columns for subplots
    num_clusters = len(cluster_sensors)
    num_delays = len(delays)
    
    num_columns = num_clusters
    num_rows = num_delays
    
    # Create subplots
    fig = make_subplots(
        rows=num_rows, 
        cols=num_columns, 
        subplot_titles=[f'Cluster {cluster} - Delay {delay} us' for delay in delays for cluster in cluster_sensors.keys()]
    )

    for i, cluster in enumerate(cluster_sensors.keys()):
        sensors = cluster_sensors[cluster]
        cluster_df = grouped_df[grouped_df['Sensor ID'].isin(sensors)]
        
        for j, delay in enumerate(delays):
            delay_df = cluster_df[cluster_df['Delay (us)'] == delay]

            # Get the row and column position for the subplot
            row = j + 1
            col = i + 1

            # Adding error bars
            for sensor_id in sensors:
                sensor_data = delay_df[delay_df['Sensor ID'] == sensor_id]
                fig.add_trace(
                    go.Scatter(
                        x=sensor_data['Range (cm)'],
                        y=sensor_data['mean_ping_time'],
                        mode='lines+markers',
                        name=f'Sensor {sensor_id} (Delay {delay} us)',
                        error_y=dict(
                            type='data',
                            array=sensor_data['std_ping_time'],
                            visible=True
                        )
                    ),
                    row=row, col=col
                )

            # Plot reference line
            ranges = np.linspace(delay_df['Range (cm)'].min(), delay_df['Range (cm)'].max(), 100)
            reference_ping_times = 57 * ranges
            fig.add_trace(
                go.Scatter(
                    x=ranges,
                    y=reference_ping_times,
                    mode='lines',
                    line=dict(color='red', dash='dash'),
                    name='Reference Line'
                ),
                row=row, col=col
            )

    fig.update_layout(
        height=500 * num_rows,  # Adjust height based on the number of delays
        width=800 * num_columns,  # Adjust width based on the number of clusters
        showlegend=False,
        title_text="Side-by-Side Comparison of Clusters Across All Delays"
    )

    fig.show()

def visualize_cluster_delay_side_by_side(df, clusters_to_compare, delays=[3000, 6000, 8000, 10000, 16800]):
    """
    Compare multiple clusters across all specified delays side by side.

    Parameters:
    df (DataFrame): The DataFrame containing the data, including clustering information.
    clusters_to_compare (list): List of cluster labels to compare side-by-side.
    delays (list): List of delays to compare.
    """
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)

    # Dictionary to store sensors grouped by cluster
    cluster_sensors = {cluster: df[df["cluster"] == cluster]["Sensor ID"].unique() for cluster in clusters_to_compare}

    # Visualize side-by-side comparisons for the selected clusters and delays
    visualize_lineplot_ping_time_with_variability_side_by_side(all_cleaned_df, cluster_sensors, delays)


In [160]:
visualize_cluster_delay(df_nofreq_50_gmm_15,delay_pos=0)

In [161]:
visualize_cluster_delay(df_nofreq_50_gmm_15,delay_pos=3)

In [162]:
visualize_cluster_delay(df_nofreq_50_gmm_15,delay_pos=4)

In [163]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_nofreq_50_gmm_10, clusters_to_compare=[0,2])


In [164]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_nofreq_50_gmm_10, clusters_to_compare=[4, 9])


In [165]:
# Assuming df is your dataset containing the clustering information
visualize_cluster_delay_side_by_side(df_nofreq_50_gmm_10, clusters_to_compare=[1, 2])
